In [1]:
import json
import sys
import glob
import torch
sys.path.append('../')
import os
from transformers import *
from kaiser.src import utils
from kaiser.src import dataio
from kaiser.src.modeling import BertForJointShallowSemanticParsing, FrameBERT
from torch.utils.data import TensorDataset, DataLoader, RandomSampler, SequentialSampler
from kaiser.src.prototypical_loss import prototypical_loss as loss_fn
import torch
from torch import nn
from torch.optim import Adam
from tqdm import tqdm, trange
from sklearn.metrics import accuracy_score
from seqeval.metrics import f1_score, precision_score, recall_score

import torch.nn.functional as F
from torch.nn import CrossEntropyLoss

from kaiser.src.prototypical_loss import prototypical_loss as loss_fn
from kaiser.src import prototypical_batch_sampler

device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")
n_gpu = torch.cuda.device_count()
if device != "cpu":
    torch.cuda.set_device(0)
# device = torch.device('cpu')
# torch.cuda.set_device(device)
# torch.backends.cudnn.deterministic = True
# torch.backends.cudnn.benchmark = True

import numpy as np
import random
np.random.seed(0)   
random.seed(0)
import random

from torch import autograd
torch.cuda.empty_cache()

from collections import Counter, OrderedDict

Using TensorFlow backend.


### Korean FrameNet ###
	# contact: hahmyg@kaist, hahmyg@gmail.com #



In [2]:
# 실행시간 측정 함수
import time

_start_time = time.time()

def tic():
    global _start_time 
    _start_time = time.time()

def tac():
    t_sec = round(time.time() - _start_time)
    (t_min, t_sec) = divmod(t_sec,60)
    (t_hour,t_min) = divmod(t_min,60)
    
    result = '{}hour:{}min:{}sec'.format(t_hour,t_min,t_sec)
    return result

In [3]:
try:
    dir_path = os.path.dirname(os.path.abspath( __file__ ))
except:
    dir_path = '.'

In [4]:
bert_io = utils.for_BERT(mode='train', language='multi')

used dictionary:
	 /disk/kaiser/kaiser/src/../koreanframenet/resource/info/mul_lu2idx.json
	 /disk/kaiser/kaiser/src/../koreanframenet/resource/info/mul_lufrmap.json
	 /disk/kaiser/kaiser/src/../koreanframenet/resource/info/mul_bio_frargmap.json


In [5]:
frameBERT_dir = '/disk/data/models/frameBERT/frameBERT_en'

frameBERT = FrameBERT.from_pretrained(frameBERT_dir,
                                      num_senses = len(bert_io.sense2idx), 
                                      num_args = len(bert_io.bio_arg2idx),
                                      lufrmap=bert_io.lufrmap, 
                                      frargmap = bert_io.bio_frargmap)
frameBERT.to(device)
frameBERT.eval()

FrameBERT(
  (bert): BertModel(
    (embeddings): BertEmbeddings(
      (word_embeddings): Embedding(119547, 768, padding_idx=0)
      (position_embeddings): Embedding(512, 768)
      (token_type_embeddings): Embedding(2, 768)
      (LayerNorm): LayerNorm((768,), eps=1e-12, elementwise_affine=True)
      (dropout): Dropout(p=0.1, inplace=False)
    )
    (encoder): BertEncoder(
      (layer): ModuleList(
        (0): BertLayer(
          (attention): BertAttention(
            (self): BertSelfAttention(
              (query): Linear(in_features=768, out_features=768, bias=True)
              (key): Linear(in_features=768, out_features=768, bias=True)
              (value): Linear(in_features=768, out_features=768, bias=True)
              (dropout): Dropout(p=0.1, inplace=False)
            )
            (output): BertSelfOutput(
              (dense): Linear(in_features=768, out_features=768, bias=True)
              (LayerNorm): LayerNorm((768,), eps=1e-12, elementwise_affine=True)
 

In [6]:
print('... loading FN data')
tic()
trn, dev, tst = dataio.load_data(srl='framenet', language='en', exem=True)
# trn = random.sample(trn, k=500)
# dev = random.sample(trn, k=100)
# tst = random.sample(tst, k=100)
print('... converting FN data to BERT')
trn_data = bert_io.convert_to_bert_input_JointShallowSemanticParsing(trn)
dev_data = bert_io.convert_to_bert_input_JointShallowSemanticParsing(dev)
tst_data = bert_io.convert_to_bert_input_JointShallowSemanticParsing(tst)

with open('./koreanframenet/resource/info/fn1.7_frame2idx.json', 'r') as f:
    frame2idx = json.load(f)
with open('./koreanframenet/resource/info/fn1.7_frame_definitions.json', 'r') as f:
    frame2definition = json.load(f)

def_data, def_y = bert_io.convert_to_bert_input_label_definition(frame2definition, frame2idx)
print(tac())

... loading FN data
# of instances in trn: 19391
# of instances in dev: 2272
# of instances in tst: 6714
data example: [['Greece', 'wildfires', 'force', 'thousands', 'to', '<tgt>', 'evacuate', '</tgt>'], ['_', '_', '_', '_', '_', '_', 'evacuate.v', '_'], ['_', '_', '_', '_', '_', '_', 'Escaping', '_'], ['O', 'O', 'O', 'B-Escapee', 'O', 'X', 'O', 'X']]
... converting FN data to BERT
0hour:0min:9sec


In [7]:
class MLP(nn.Module):
    def __init__(self):
        super(MLP, self).__init__()
        self.layers = nn.Sequential(
            nn.Linear(768, 768),
            nn.ReLU(),
            nn.Linear(768, 768)
        )
        
    def forward(self, x):
        x = x.view(x.size(0), -1)
        x = self.layers(x)
        return x

In [8]:
def save_list_to_file(path, thelist):
    with open(path, 'w') as f:
        for item in thelist:
            f.write("%s\n" % item)

def get_y(data):
    with open('./koreanframenet/resource/info/fn1.7_frame2idx.json', 'r') as f:
        frame2idx = json.load(f)
    y = []
    for instance in data:
        frame = False
        for i in instance[2]:
            if i != '_':
                frame = i
                break
        frameidx = frame2idx[frame]
        y.append(frameidx)
    return tuple(y)

def get_target_frames(input_data):
    all_y = dict(Counter(get_y(input_data)))
    target_frames = []
    for i in all_y:
        count = all_y[i]
        if count >= 5:
            target_frames.append(i)
            
    return target_frames
            
trn_target_frames = get_target_frames(trn)
dev_target_frames = get_target_frames(dev)
tst_target_frames = get_target_frames(tst)

print('trn_target_frames:', len(trn_target_frames))
print('dev_target_frames:', len(dev_target_frames))
print('tst_target_frames:', len(tst_target_frames))

trn_target_frames: 89
dev_target_frames: 13
tst_target_frames: 17


In [9]:
trn_batch_sampler = prototypical_batch_sampler.PrototypicalBatchSampler(classes_per_it=60, 
                                                                        num_support=5,
                                                                        target_frames=trn_target_frames, 
                                                                        def_data=def_data, def_y=def_y)

# trn_batch_sampler = prototypical_batch_sampler.PrototypicalBatchSampler(classes_per_it=4, 
#                                                                         num_support=2,
#                                                                         target_frames=trn_target_frames, 
#                                                                         def_data=def_data, def_y=def_y)

used dictionary:
	 /disk/kaiser/kaiser/src/../koreanframenet/resource/info/mul_lu2idx.json
	 /disk/kaiser/kaiser/src/../koreanframenet/resource/info/mul_lufrmap.json
	 /disk/kaiser/kaiser/src/../koreanframenet/resource/info/mul_bio_frargmap.json


In [10]:
dev_batch_sampler = prototypical_batch_sampler.PrototypicalBatchSampler(classes_per_it=5, 
                                                                        num_support=5, 
                                                                        target_frames=dev_target_frames, 
                                                                        def_data=def_data, def_y=def_y)

# dev_batch_sampler = prototypical_batch_sampler.PrototypicalBatchSampler(classes_per_it=4, 
#                                                                         num_support=2, 
#                                                                         target_frames=dev_target_frames, 
#                                                                         def_data=def_data, def_y=def_y)

used dictionary:
	 /disk/kaiser/kaiser/src/../koreanframenet/resource/info/mul_lu2idx.json
	 /disk/kaiser/kaiser/src/../koreanframenet/resource/info/mul_lufrmap.json
	 /disk/kaiser/kaiser/src/../koreanframenet/resource/info/mul_bio_frargmap.json


In [11]:
tst_batch_sampler = prototypical_batch_sampler.PrototypicalBatchSampler(classes_per_it=5, 
                                                                        num_support=5, 
                                                                        target_frames=tst_target_frames, 
                                                                        def_data=def_data, def_y=def_y)

# tst_batch_sampler = prototypical_batch_sampler.PrototypicalBatchSampler(classes_per_it=4, 
#                                                                         num_support=2, 
#                                                                         target_frames=tst_target_frames, 
#                                                                         def_data=def_data, def_y=def_y)

used dictionary:
	 /disk/kaiser/kaiser/src/../koreanframenet/resource/info/mul_lu2idx.json
	 /disk/kaiser/kaiser/src/../koreanframenet/resource/info/mul_lufrmap.json
	 /disk/kaiser/kaiser/src/../koreanframenet/resource/info/mul_bio_frargmap.json
used dictionary:
	 /disk/kaiser/kaiser/src/../koreanframenet/resource/info/mul_lu2idx.json
	 /disk/kaiser/kaiser/src/../koreanframenet/resource/info/mul_lufrmap.json
	 /disk/kaiser/kaiser/src/../koreanframenet/resource/info/mul_bio_frargmap.json


In [12]:
def get_embs_from_episode(episode):
    support_embs = []
    query_embs = []
    
    support_y, query_y = [],[]
    
    for class_indice in episode:
        support_examples, query_examples = class_indice

        query_inputs, _, query_token_type_ids, query_masks = query_examples[0][0]
        query_inputs = query_inputs.view(1,len(query_inputs)).to(device)
        query_token_type_ids = query_token_type_ids.view(1,len(query_token_type_ids)).to(device)
        query_masks = query_masks.view(1,len(query_masks)).to(device)
        
        query_frame = query_examples[0][1]
        query_y.append(query_frame)
    
        with torch.no_grad():
            _, query_emb = frameBERT(query_inputs, 
                                  token_type_ids=query_token_type_ids, 
                                  attention_mask=query_masks)
            query_emb = query_emb.view(-1)
        query_embs.append(query_emb)
        
        support_inputs, support_token_type_ids, support_masks = [],[],[]
        for i in range(len(support_examples)):
            support_input, _, _, _, _, support_token_type_id, support_mask = support_examples[i][0]
            support_inputs.append(support_input)
            support_token_type_ids.append(support_token_type_id)
            support_masks.append(support_mask)
            
            support_frame = support_examples[i][1]
            support_y.append(support_frame)
            
        support_inputs = torch.stack(support_inputs).to(device)
        support_token_type_ids = torch.stack(support_token_type_ids).to(device)
        support_masks = torch.stack(support_masks).to(device)
        
        with torch.no_grad():
            _, support_emb = frameBERT(support_inputs, 
                                  token_type_ids=support_token_type_ids, 
                                  attention_mask=support_masks)
        support_embs.append(support_emb)
        
    support_embs = torch.stack(support_embs)
    support_embs = support_embs.view(-1, 768)
    query_embs = torch.stack(query_embs)
    
    support_y = tuple(support_y)
    query_y = tuple(query_y)
    
    return support_embs, query_embs, support_y, query_y

In [13]:
def train(trn_batch, dev_batch,  best_model_path, last_model_path, model=False):
    # load optimizer
    FULL_FINETUNING = True
    if FULL_FINETUNING:
        param_optimizer = list(model.named_parameters())
        no_decay = ['bias', 'gamma', 'beta']
        optimizer_grouped_parameters = [
            {'params': [p for n, p in param_optimizer if not any(nd in n for nd in no_decay)],
             'weight_decay_rate': 0.01},
            {'params': [p for n, p in param_optimizer if any(nd in n for nd in no_decay)],
             'weight_decay_rate': 0.0}
        ]
    else:
        param_optimizer = list(model.classifier.named_parameters()) 
        optimizer_grouped_parameters = [{"params": [p for n, p in param_optimizer]}]
    optimizer = Adam(optimizer_grouped_parameters, lr=3e-5)
    max_grad_norm = 1.0
    
    train_loss = []
    train_acc = []
    val_loss = []
    val_acc = []
    best_acc = 0
    
    for epoch in range(TRN_EPOCHS):
        model.train()
        for episode in trn_batch:
            support_embs, query_embs, support_y, query_y = get_embs_from_episode(episode)
            
            support_embs = model(support_embs)
            query_embs = model(query_embs)

            loss, acc = loss_fn(support_embs, query_embs, support_y, query_y, len(support_y))

            loss.backward()
            torch.nn.utils.clip_grad_norm_(parameters=model.parameters(), max_norm=max_grad_norm)
            optimizer.step()
            model.zero_grad()
            
            train_loss.append(loss.item())
            train_acc.append(acc.item())

            
        avg_loss = np.mean(train_loss[-100:])
        avg_acc = np.mean(train_acc[-100:])
        print('Avg Train Loss: {}, Avg Train Acc: {}'.format(avg_loss, avg_acc))
        
        model.eval()
        for episode in dev_batch:
            support_embs, query_embs, support_y, query_y = get_embs_from_episode(episode)
            support_embs = model(support_embs)
            query_embs = model(query_embs)
            
            loss_val, acc_val = loss_fn(support_embs, query_embs, support_y, query_y, len(support_y))
            
            val_loss.append(loss_val.item())
            val_acc.append(acc_val.item())

            
        avg_loss = np.mean(val_loss[-100:])
        avg_acc = np.mean(val_acc[-100:])
        
        postfix = ' (Best)' if avg_acc >= best_acc else ' (Best: {})'.format(
            best_acc)
        print('Avg Val Loss: {}, Avg Val Acc: {}{}'.format(
            avg_loss, avg_acc, postfix))
        
        if avg_acc >= best_acc:
            torch.save(model.state_dict(), best_model_path)
            best_acc = avg_acc
            best_state = model.state_dict()

    torch.save(model.state_dict(), last_model_path)

    for name in ['train_loss', 'train_acc', 'val_loss', 'val_acc']:
        save_list_to_file(os.path.join('/disk/data/models/framenet/prototype_mlp/',
                                       name + '.txt'), locals()[name])
        
        
        
best_model_path = '/disk/data/models/framenet/prototype_mlp/best_model.pth'
last_model_path = '/disk/data/models/framenet/prototype_mlp/last_model.pth'
trn_y = get_y(trn)
dev_y = get_y(dev)

trn_batch = trn_batch_sampler.gen_batch(trn_data, trn_y)
dev_batch = dev_batch_sampler.gen_batch(dev_data, dev_y)

TRN_EPOCHS = 100
mlp_model = MLP()
mlp_model.to(device)

print('\n...training')
train(trn_batch, dev_batch, best_model_path, last_model_path, model=mlp_model)
print(tac())


...training

support_idxs
tensor([[0, 1],
        [2, 3],
        [4, 5],
        [6, 7]])

support_y
(71, 71, 782, 782, 914, 914, 92, 92)

query_y
(71, 782, 914, 92)

prototypes
tensor([[-0.1698, -0.3690,  0.2898,  ...,  0.1085,  0.2475,  0.1896],
        [-0.1207, -0.0452, -0.0064,  ...,  0.1706, -0.0849, -0.0826],
        [-0.3215,  0.1236,  0.0600,  ..., -0.0386,  0.0183,  0.0857],
        [-0.0207,  0.0866,  0.2288,  ..., -0.0472, -0.2688, -0.3009]],
       device='cuda:0', grad_fn=<CopyBackwards>)

query_embs
tensor([[-0.0486, -0.0079,  0.2983,  ..., -0.0385, -0.0897,  0.1057],
        [ 0.0096, -0.1058,  0.2724,  ..., -0.0191, -0.1441,  0.1321],
        [-0.0884, -0.0545,  0.2788,  ..., -0.0273, -0.1014,  0.1031],
        [-0.1170,  0.0979,  0.2405,  ...,  0.0127,  0.0974,  0.0813]],
       device='cuda:0', grad_fn=<AddmmBackward>)

dists
tensor([[26.4348, 25.0661, 39.5270, 29.2440],
        [29.8191, 26.8048, 41.4917, 29.9901],
        [26.2317, 24.3571, 39.3342, 29.6797],
   


support_idxs
tensor([[0, 1],
        [2, 3],
        [4, 5],
        [6, 7]])

support_y
(1176, 1176, 1121, 1121, 170, 170, 491, 491)

query_y
(1176, 1121, 170, 491)

prototypes
tensor([[-1.0206e-01,  3.0199e-02,  1.4105e-01,  ...,  1.9418e-01,
          3.7729e-02,  3.6498e-02],
        [-1.7439e-01,  1.2192e-01,  1.3825e-01,  ...,  1.0011e-01,
         -1.3045e-01, -2.2443e-01],
        [-2.5921e-01, -1.8710e-01,  4.0672e-02,  ...,  1.9691e-01,
          6.2979e-02,  1.8965e-04],
        [-3.4592e-01, -1.2251e-01,  3.6375e-01,  ...,  3.4946e-01,
          1.0356e-01,  2.2065e-01]], device='cuda:0', grad_fn=<CopyBackwards>)

query_embs
tensor([[-0.1073, -0.0632,  0.3642,  ...,  0.0164, -0.1590,  0.2639],
        [-0.0510, -0.0147,  0.3159,  ..., -0.0152,  0.0032,  0.1817],
        [-0.0006, -0.1316,  0.3069,  ..., -0.0315, -0.1684,  0.0883],
        [-0.2377,  0.0053,  0.2342,  ...,  0.1133, -0.0030,  0.1005]],
       device='cuda:0', grad_fn=<AddmmBackward>)

dists
tensor([[30.9716,


support_idxs
tensor([[0, 1],
        [2, 3],
        [4, 5],
        [6, 7]])

support_y
(810, 810, 356, 356, 196, 196, 275, 275)

query_y
(810, 356, 196, 275)

prototypes
tensor([[ 0.0419, -0.0934,  0.1349,  ..., -0.0765, -0.1777, -0.1245],
        [-0.4617,  0.1715,  0.1620,  ...,  0.2249,  0.1499, -0.3896],
        [-0.3382,  0.1246,  0.3165,  ...,  0.0065,  0.4605,  0.4388],
        [-0.1435,  0.2697,  0.1077,  ..., -0.0526,  0.0381, -0.0073]],
       device='cuda:0', grad_fn=<CopyBackwards>)

query_embs
tensor([[ 0.0259, -0.0282,  0.1504,  ..., -0.0243, -0.0383,  0.1776],
        [-0.0763,  0.0694,  0.3029,  ...,  0.0120,  0.0427,  0.1460],
        [ 0.0512,  0.0220,  0.2667,  ..., -0.0589,  0.0537,  0.0742],
        [-0.0383, -0.0995,  0.2446,  ...,  0.0018, -0.0260,  0.2216]],
       device='cuda:0', grad_fn=<AddmmBackward>)

dists
tensor([[30.0845, 32.5269, 28.7207, 35.0344],
        [29.2154, 32.5822, 28.7413, 32.7916],
        [28.9624, 33.3731, 29.6203, 33.3511],
        [3


support_idxs
tensor([[0, 1],
        [2, 3],
        [4, 5],
        [6, 7]])

support_y
(900, 900, 907, 907, 1109, 1109, 408, 408)

query_y
(900, 907, 1109, 408)

prototypes
tensor([[-0.1058, -0.2801,  0.1062,  ...,  0.1412, -0.1566, -0.1861],
        [-0.2879, -0.4671, -0.2511,  ..., -0.2267, -0.0101,  0.0368],
        [-0.2985, -0.3042,  0.2954,  ...,  0.1594,  0.1077,  0.2420],
        [-0.2637, -0.4458,  0.2921,  ...,  0.3181,  0.4136,  0.1020]],
       device='cuda:0', grad_fn=<CopyBackwards>)

query_embs
tensor([[-0.0424, -0.0416,  0.2084,  ..., -0.0414,  0.0526,  0.1787],
        [-0.1551,  0.0226,  0.2829,  ..., -0.0323, -0.0399,  0.1989],
        [-0.1348, -0.1012,  0.2177,  ...,  0.0177, -0.0238,  0.2629],
        [-0.0440, -0.0663,  0.2579,  ..., -0.0081, -0.0519,  0.2366]],
       device='cuda:0', grad_fn=<AddmmBackward>)

dists
tensor([[31.4946, 27.9257, 28.6819, 28.8445],
        [33.1651, 28.6297, 29.9029, 29.1931],
        [29.9322, 27.6988, 28.4182, 29.9902],
       


support_idxs
tensor([[0, 1],
        [2, 3],
        [4, 5],
        [6, 7]])

support_y
(215, 215, 170, 170, 793, 793, 901, 901)

query_y
(215, 170, 793, 901)

prototypes
tensor([[-0.3726,  0.0894,  0.2445,  ...,  0.1113,  0.1018,  0.0837],
        [-0.2397, -0.1814,  0.0599,  ...,  0.1809,  0.0585,  0.0039],
        [ 0.0581,  0.0164, -0.2323,  ..., -0.4535,  0.0187,  0.2610],
        [-0.0864, -0.2203,  0.1036,  ...,  0.0549, -0.1640, -0.2812]],
       device='cuda:0', grad_fn=<CopyBackwards>)

query_embs
tensor([[-0.0493, -0.0890,  0.1806,  ..., -0.0664,  0.0297,  0.0712],
        [-0.0274, -0.1393,  0.2840,  ..., -0.0592, -0.1526,  0.0912],
        [-0.0878, -0.0103,  0.2686,  ..., -0.0806,  0.0250,  0.1642],
        [-0.0486, -0.1239,  0.2530,  ..., -0.0006, -0.0021,  0.2320]],
       device='cuda:0', grad_fn=<AddmmBackward>)

dists
tensor([[31.1978, 30.8820, 34.1362, 29.2286],
        [35.2550, 30.8550, 37.8942, 28.6552],
        [33.8139, 32.6068, 35.4495, 30.1335],
        [3

...


support_idxs
tensor([[0, 1],
        [2, 3],
        [4, 5],
        [6, 7]])

support_y
(356, 356, 1090, 1090, 605, 605, 993, 993)

query_y
(356, 1090, 605, 993)

prototypes
tensor([[-0.4933,  0.1776,  0.1525,  ...,  0.1841,  0.2849, -0.4676],
        [ 0.0729, -0.0522,  0.3437,  ..., -0.2556, -0.2359,  0.0907],
        [ 0.0155, -0.3194,  0.0638,  ..., -0.0528,  0.0469,  0.0179],
        [-0.0798, -0.2487,  0.3638,  ...,  0.2485, -0.4500, -0.1138]],
       device='cuda:0', grad_fn=<CopyBackwards>)

query_embs
tensor([[-0.0930,  0.0179,  0.2659,  ...,  0.0020,  0.1973, -0.0720],
        [-0.0220, -0.3068,  0.3137,  ..., -0.1192, -0.0955,  0.1599],
        [-0.0711, -0.1421,  0.2356,  ..., -0.1754,  0.0406,  0.0527],
        [-0.0512, -0.1661,  0.2867,  ..., -0.0787,  0.0070,  0.0778]],
       device='cuda:0', grad_fn=<AddmmBackward>)

dists
tensor([[23.6153, 58.4139, 39.2941, 35.4158],
        [53.0886, 19.1953, 39.3204, 30.7864],
        [36.9422, 41.7373, 21.3908, 33.8216],
       


support_idxs
tensor([[0, 1],
        [2, 3],
        [4, 5],
        [6, 7]])

support_y
(196, 196, 898, 898, 1080, 1080, 357, 357)

query_y
(196, 898, 1080, 357)

prototypes
tensor([[-0.1999,  0.2251,  0.3676,  ...,  0.0217,  0.6119,  0.3923],
        [-0.1273,  0.3576,  0.2680,  ..., -0.2583, -0.0198, -0.2665],
        [ 0.2610,  0.1995,  0.3330,  ..., -0.0770,  0.0805,  0.2464],
        [-0.0682, -0.2146, -0.0380,  ..., -0.1838,  0.0081,  0.0577]],
       device='cuda:0', grad_fn=<CopyBackwards>)

query_embs
tensor([[ 0.0500,  0.0090,  0.2125,  ..., -0.0592,  0.2728, -0.1331],
        [ 0.1133,  0.1736,  0.2402,  ..., -0.0585,  0.0760, -0.0405],
        [ 0.0440, -0.1263,  0.3164,  ..., -0.1304, -0.0998,  0.1776],
        [-0.1028, -0.1551,  0.2305,  ..., -0.1113,  0.1099,  0.0194]],
       device='cuda:0', grad_fn=<AddmmBackward>)

dists
tensor([[23.2993, 38.4383, 40.8782, 37.4518],
        [36.0433, 26.8386, 46.9868, 39.9030],
        [38.5899, 38.8128, 20.8802, 37.0236],
       


support_idxs
tensor([[0, 1],
        [2, 3],
        [4, 5],
        [6, 7]])

support_y
(196, 196, 1129, 1129, 749, 749, 157, 157)

query_y
(196, 1129, 749, 157)

prototypes
tensor([[-0.2000,  0.2252,  0.3677,  ...,  0.0218,  0.6122,  0.3925],
        [-0.2759,  0.0647,  0.2498,  ..., -0.1547,  0.2342,  0.1241],
        [-0.0528, -0.4178,  0.2317,  ..., -0.0248, -0.3227, -0.1705],
        [-0.0559, -0.3999,  0.1986,  ..., -0.2412,  0.1039, -0.1759]],
       device='cuda:0', grad_fn=<CopyBackwards>)

query_embs
tensor([[ 0.0499,  0.0091,  0.2128,  ..., -0.0589,  0.2728, -0.1331],
        [-0.0249,  0.1133,  0.1160,  ..., -0.1418,  0.2598, -0.0453],
        [ 0.0658, -0.3502,  0.2854,  ..., -0.1196, -0.0543,  0.1198],
        [-0.0809, -0.2087,  0.1589,  ..., -0.0664,  0.0515,  0.1510]],
       device='cuda:0', grad_fn=<AddmmBackward>)

dists
tensor([[23.3121, 40.9289, 43.0475, 35.8294],
        [39.8845, 25.0198, 47.7523, 47.3733],
        [41.1641, 49.2513, 22.2700, 36.4461],
       


support_idxs
tensor([[0, 1],
        [2, 3],
        [4, 5],
        [6, 7]])

support_y
(1005, 1005, 71, 71, 749, 749, 182, 182)

query_y
(1005, 71, 749, 182)

prototypes
tensor([[ 0.2853,  0.0325,  0.2294,  ..., -0.1926,  0.4647,  0.1999],
        [-0.1884, -0.3930,  0.3901,  ...,  0.0439,  0.3441, -0.0302],
        [-0.0708, -0.4672,  0.2065,  ...,  0.0347, -0.3619, -0.1752],
        [ 0.0684, -0.3031,  0.2202,  ...,  0.4062, -0.1883,  0.2173]],
       device='cuda:0', grad_fn=<CopyBackwards>)

query_embs
tensor([[ 0.1353,  0.1115,  0.1392,  ..., -0.2420,  0.2507,  0.0898],
        [-0.1128, -0.1263,  0.2449,  ..., -0.1597,  0.1072, -0.0375],
        [ 0.0658, -0.3501,  0.2856,  ..., -0.1193, -0.0542,  0.1198],
        [ 0.0674,  0.0834,  0.1873,  ...,  0.0518,  0.1115,  0.0482]],
       device='cuda:0', grad_fn=<AddmmBackward>)

dists
tensor([[21.6099, 31.9397, 52.2389, 45.0556],
        [33.1895, 21.5627, 48.3029, 40.5155],
        [47.2376, 48.3213, 24.9629, 35.6241],
        [4

KeyboardInterrupt: 

In [ ]:
def test(tst_batch, model_path=False):
    avg_acc = list()
    model = MLP()
    model.to(device)
    model.load_state_dict(torch.load(model_path))
    for epoch in range(10):
        model.eval()
        for episode in tst_batch:
            support_embs, query_embs, support_y, query_y = get_embs_from_episode(episode)

            support_embs = model(support_embs)
            query_embs = model(query_embs)

            _, acc_val = loss_fn(support_embs, query_embs, support_y, query_y, len(support_y))

            avg_acc.append(acc_val.item())
        
    avg_acc = np.mean(avg_acc)
    print('Test Acc: {}'.format(avg_acc))
    with open('/disk/data/models/framenet/prototype_mlp/test_acc.txt','w') as f:
        f.write(str(avg_acc))
        
best_model_path = '/disk/data/models/framenet/prototype_mlp/best_model.pth'
tst_y = get_y(tst)
tst_batch = tst_batch_sampler.gen_batch(tst_data, tst_y)


print('\n...testing')
test(tst_batch, model_path=best_model_path)
print(tac())